In [2]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import dgl
from dgl.nn import ChebConv
import networkx as nx
import networkx.algorithms.community as nx_comm
import numpy as np
import pandas as pd
import numpy.linalg as alg
import os
from tqdm import tqdm
from functools import reduce
import argparse


def node_connects_cluster(node):
    return set(map(lambda x: inverse_cluster_dict[x], list(g[node]))).union(set([inverse_cluster_dict[node]]))



DGL backend not selected or invalid.  Assuming PyTorch for now.


Setting the default backend to "pytorch". You can change it in the ~/.dgl/config.json file or export the DGLBACKEND environment variable.  Valid options are: pytorch, mxnet, tensorflow (all lowercase)


/root/miniconda3/envs/myconda/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:

path = 'Dataset/socfb-Stanford3.mtx'

df = pd.read_table(path, skiprows=1, names = ["source", "target"], sep=" ")
g = nx.from_pandas_edgelist(df)

# calculate basic elements
num_nodes = g.number_of_nodes()
num_edges = g.number_of_edges()
degs = [g.degree[i] for i in g.nodes]
avg_deg = sum(degs)/len(degs)

res = 10


# clustering
# generally, we fix the outcome of clustering
clusters = nx_comm.louvain_communities(g, seed = 10, resolution=res)
clusters = sorted(clusters, key = len, reverse=True)
cluster_sizes = list(map(len, clusters))
num_cluster = len(clusters)

# dict: from node to its cluster
inverse_cluster_dict = {
    node: cl for cl in range(num_cluster) for node in clusters[cl]
}

# dict: from node to its connected cluster
node_to_connected_clusters = {
    node: node_connects_cluster(node) for node in range(1, num_nodes + 1)
}


for i in g.nodes:
    g.nodes[i]["deg"] = g.degree[i]

rev_cluster_sizes = cluster_sizes[::-1]
rev_clusters = clusters[::-1]
rev_cluster_sizes = np.array(rev_cluster_sizes)


In [4]:
dgl_G = dgl.from_networkx(g)

In [5]:
ramps = [0.02, 0.05, 0.1, 0.25, 0.5]
# ramps = [0.02, 0.5]
repeat_num = 1000

In [6]:

class GCN(nn.Module):
    def __init__(self):
        super().__init__()
        self.conv1 = dgl.nn.ChebConv(2, 16, 2)
        self.conv2 = dgl.nn.ChebConv(16, 16, 1)
        self.conv3 = dgl.nn.ChebConv(16, 1, 1)

    def forward(self, g, features):
        x = self.conv1(g, features)
        x = self.conv2(g, x)
        x = self.conv3(g, x)
        return x
        

In [7]:
def po_linear_model_square_expo(graph, alpha=1, beta=1, sigma=0.1, gamma=2):    
    for i in graph.nodes:
        graph.nodes[i]["y"] = alpha + beta * graph.nodes[i]["z"] + sigma * np.random.normal() +  gamma * (sum([graph.nodes[ngbr]['z'] for ngbr in graph[i]])/graph.degree[i])**2   

In [8]:
# unit-level

GATE_hat_list = np.zeros((repeat_num, len(ramps)))
     
for seed in tqdm(range(repeat_num)):    
    np.random.seed(seed)     
    rollout_index = np.random.uniform(0, 1, size=(num_nodes,))   
    
    for num_step in range(len(ramps)): 
        print(f"Seed: {seed}")
        torch.manual_seed(2)
        p_list = ramps[num_step:]        
        g_feat_list = []
        y_list = []
        
        for p in p_list:
            z = (rollout_index < np.quantile(rollout_index, p))            
            nx.set_node_attributes(g, 0, "z")
            nx.set_node_attributes(g, {unit:1 for unit in range(num_nodes) if z[unit]}, "z")            
                    
            po_linear_model_square_expo(g, gamma = 1)            
            g_feat_list.append(torch.tensor([[g.nodes[n]['z'], g.nodes[n]['deg']] for n in g.nodes], dtype=torch.float))
            y_list.append(torch.tensor([[g.nodes[n]['y']] for n in g.nodes], dtype=torch.float).reshape(-1))
    
        # Instantiate the model and optimizer
        model = GCN()    
        optimizer = torch.optim.Adam(model.parameters(), lr=0.004)        
    
        # Train the model
        for epoch in range(400):
            for i in range(len(p_list)):
                model.train()
                optimizer.zero_grad()
                out = model(dgl_G, g_feat_list[i])
                loss = F.mse_loss(out.squeeze(), y_list[i])  
                loss.backward()
                optimizer.step()
            
                if epoch % 50 == 0:
                    print(f'Epoch {epoch}, Treat Prop: {p_list[i]:.2f}, Loss: {loss:.4f}')
    
        print(loss.item())
        g_feat = g_feat_list[0]
    
        g_feat[:,0] = 0
        global_control_pred = model(dgl_G, g_feat).detach().numpy()
    
        g_feat[:,0] = 1
        global_treat_pred = model(dgl_G, g_feat).detach().numpy()
    
        GATE_hat = global_treat_pred.mean() - global_control_pred.mean()
    
        GATE_hat_list[seed, num_step] = GATE_hat
        
    torch.save(GATE_hat_list, "Result/Square_expo_CR_unit.pkl")


  0%|          | 0/1000 [00:00<?, ?it/s]

Seed: 0


/root/miniconda3/envs/myconda/lib/python3.10/site-packages/dgl/nn/pytorch/conv/chebconv.py:108: DGLWarning: lambda_max is not provided, using default value of 2.  Please use dgl.laplacian_lambda_max to compute the eigenvalues.
  dgl_warning(


Epoch 0, Treat Prop: 0.02, Loss: 8.0783
Epoch 0, Treat Prop: 0.05, Loss: 2.3958
Epoch 0, Treat Prop: 0.10, Loss: 1.1629
Epoch 0, Treat Prop: 0.25, Loss: 1.5885
Epoch 0, Treat Prop: 0.50, Loss: 2.7489
Epoch 50, Treat Prop: 0.02, Loss: 0.0653
Epoch 50, Treat Prop: 0.05, Loss: 0.1023
Epoch 50, Treat Prop: 0.10, Loss: 0.0899
Epoch 50, Treat Prop: 0.25, Loss: 0.1411
Epoch 50, Treat Prop: 0.50, Loss: 0.4180
Epoch 100, Treat Prop: 0.02, Loss: 0.0357
Epoch 100, Treat Prop: 0.05, Loss: 0.0185
Epoch 100, Treat Prop: 0.10, Loss: 0.0420
Epoch 100, Treat Prop: 0.25, Loss: 0.0430
Epoch 100, Treat Prop: 0.50, Loss: 0.0692
Epoch 150, Treat Prop: 0.02, Loss: 0.0304
Epoch 150, Treat Prop: 0.05, Loss: 0.0151
Epoch 150, Treat Prop: 0.10, Loss: 0.0340
Epoch 150, Treat Prop: 0.25, Loss: 0.0396
Epoch 150, Treat Prop: 0.50, Loss: 0.0591
Epoch 200, Treat Prop: 0.02, Loss: 0.0278
Epoch 200, Treat Prop: 0.05, Loss: 0.0148
Epoch 200, Treat Prop: 0.10, Loss: 0.0327
Epoch 200, Treat Prop: 0.25, Loss: 0.0374
Epoch 2

  0%|          | 1/1000 [00:34<9:38:31, 34.75s/it]

...

0.03991233929991722
Seed: 998
Epoch 0, Treat Prop: 0.02, Loss: 8.0762
Epoch 0, Treat Prop: 0.05, Loss: 2.4036
Epoch 0, Treat Prop: 0.10, Loss: 1.1639
Epoch 0, Treat Prop: 0.25, Loss: 1.5848
Epoch 0, Treat Prop: 0.50, Loss: 2.6910
Epoch 50, Treat Prop: 0.02, Loss: 0.0674
Epoch 50, Treat Prop: 0.05, Loss: 0.1048
Epoch 50, Treat Prop: 0.10, Loss: 0.0862
Epoch 50, Treat Prop: 0.25, Loss: 0.1381
Epoch 50, Treat Prop: 0.50, Loss: 0.3972
Epoch 100, Treat Prop: 0.02, Loss: 0.0350
Epoch 100, Treat Prop: 0.05, Loss: 0.0184
Epoch 100, Treat Prop: 0.10, Loss: 0.0340
Epoch 100, Treat Prop: 0.25, Loss: 0.0436
Epoch 100, Treat Prop: 0.50, Loss: 0.0576
Epoch 150, Treat Prop: 0.02, Loss: 0.0295
Epoch 150, Treat Prop: 0.05, Loss: 0.0153
Epoch 150, Treat Prop: 0.10, Loss: 0.0324
Epoch 150, Treat Prop: 0.25, Loss: 0.0374
Epoch 150, Treat Prop: 0.50, Loss: 0.0553
Epoch 200, Treat Prop: 0.02, Loss: 0.0291
Epoch 200, Treat Prop: 0.05, Loss: 0.0150
Epoch 200, Treat Prop: 0.10, Loss: 0.0327
Epoch 200, Treat Pr

100%|█████████▉| 999/1000 [9:01:24<00:31, 31.62s/it]

0.03662976622581482
Seed: 999
Epoch 0, Treat Prop: 0.02, Loss: 8.0679
Epoch 0, Treat Prop: 0.05, Loss: 2.3940
Epoch 0, Treat Prop: 0.10, Loss: 1.1625
Epoch 0, Treat Prop: 0.25, Loss: 1.5954
Epoch 0, Treat Prop: 0.50, Loss: 2.7412
Epoch 50, Treat Prop: 0.02, Loss: 0.0709
Epoch 50, Treat Prop: 0.05, Loss: 0.1100
Epoch 50, Treat Prop: 0.10, Loss: 0.0896
Epoch 50, Treat Prop: 0.25, Loss: 0.1439
Epoch 50, Treat Prop: 0.50, Loss: 0.4194
Epoch 100, Treat Prop: 0.02, Loss: 0.0233
Epoch 100, Treat Prop: 0.05, Loss: 0.0170
Epoch 100, Treat Prop: 0.10, Loss: 0.0313
Epoch 100, Treat Prop: 0.25, Loss: 0.0339
Epoch 100, Treat Prop: 0.50, Loss: 0.0615
Epoch 150, Treat Prop: 0.02, Loss: 0.0310
Epoch 150, Treat Prop: 0.05, Loss: 0.0147
Epoch 150, Treat Prop: 0.10, Loss: 0.0345
Epoch 150, Treat Prop: 0.25, Loss: 0.0379
Epoch 150, Treat Prop: 0.50, Loss: 0.0568
Epoch 200, Treat Prop: 0.02, Loss: 0.0280
Epoch 200, Treat Prop: 0.05, Loss: 0.0144
Epoch 200, Treat Prop: 0.10, Loss: 0.0324
Epoch 200, Treat Pr

100%|██████████| 1000/1000 [9:01:55<00:00, 32.52s/it]

0.05052458122372627
